# Impact of static imperfections on our X-band linac from 100 MeV to 500 GeV and beam-based alignment

In [ ]:
import RF_Track
import numpy
import scipy
import matplotlib.pyplot as plt

## Load the lattice from appropriate scripts

In [ ]:
import scripts

## Let's define some key parameters
We use a structure to collect all relevant parameters

In [ ]:
# Structure "setup"
class Setup:
    def __init__(self):
        self.Q = -1 # single-particle charge, in units of e
        self.mass = RF_Track.electronmass # MeV/c^2
        self.population = RF_Track.nC # 50 * RF_Track.pC; % number of real particles per bunch
        
        self.sigma_t = 0.100 # mm/c
        self.sigma_pt = 0.1 # permil, momentum spread

        self.P_i = 100 # initial momentum, MeV/c
        self.P_f = 500 # final momentum, MeV/c

        self.phid = -27 # deg, phase of the RF structures
        self.mu = 60 # deg, FODO phase advance per cell

## Let's build the linac lattice
We use a standard FODO lattice, with four structures every two consecutive quadrupoles and 90 degrees phase advance per cell

In [ ]:
setup = Setup()
rf_name = 'data/TWS_Xband.dat'
LINAC = scripts.init_linac_lattice (rf_name, setup)

## Let's define and track the reference particle

In [ ]:
P0 = scripts.init_reference_particle (setup)
# Track the reference particle
P1 = LINAC.track(P0)

In [ ]:
P1.get_phase_space()

In [ ]:
LINAC.get_length()

In [ ]:
print(P0.get_phase_space('%Vx %Vy %Vz'))
print(P1.get_phase_space('%Vx %Vy %Vz'))

## ...and a bunch

In [ ]:
B0 = scripts.init_bunch(rf_name, setup)

## Let's study the impact of quadrupole misalignment

Assuming 100 $\mu$m and 100 $\mu$rad RMS pre-alignment error

In [ ]:
sigma_X = 0.100 # mm
sigma_ROLL = 0.100 # mrad

We use the method: ```LINAC.scatter_elements``` which takes
* type of element
* X, Y, Z rms misalignment in mm
* ROLL, PITCH, YAW rms misalignemnt in mrad
* the reference point: 'entrance',  'center',  'exit'

Let's simulate a few random seeds...

In [ ]:
nSeeds = 10

for i in range(nSeeds):
    print('Seed {}/{}\n'.format(i+1, nSeeds))  
    LINAC.scatter_elements('quadrupole', sigma_X, sigma_X, 0, sigma_ROLL, 0, 0, 'center')
    B1 = LINAC.track(B0)
    T = LINAC.get_transport_table('%S %emitt_x %emitt_y')  
    plt.plot(T[:,0], T[:,1], 'C00', linewidth=2)
    plt.plot(T[:,0], T[:,2], 'C01', linewidth=2)
plt.legend([r'$\epsilon_x$', r'$\epsilon_y$'])
plt.xlabel('s [m]')
plt.ylabel(r'$\epsilon_n$ [mm.mrad]')

## Let's misalign the RF structures

In [ ]:
nSeeds = 10
LINAC.align_elements() # zeros the offsets of all the elements

for i in range(nSeeds):
    print('Seed {}/{}\n'.format(i+1, nSeeds))  
    LINAC.scatter_elements('rf_element', sigma_X, sigma_X, 0, sigma_ROLL, 0, 0, 'center')
    B1 = LINAC.track(B0)
    T = LINAC.get_transport_table('%S %emitt_x %emitt_y')  
    plt.plot(T[:,0], T[:,1], 'C00', linewidth=2)
    plt.plot(T[:,0], T[:,2], 'C01', linewidth=2)
plt.legend([r'$\epsilon_x$', r'$\epsilon_y$'])
plt.xlabel('s [m]')
plt.ylabel(r'$\epsilon_n$ [mm.mrad]')

## Let's apply orbit correction

### We need to add correctors and bpms to our lattice

In [ ]:
LINAC_BBA = scripts.init_linac_lattice(rf_name, setup)

In [ ]:
R0 = LINAC_BBA.get_response_matrix(B0)

In [ ]:
fig, ax = plt.subplots(subplot_kw=dict(projection='3d'))
x, y = R0.shape
x, y = numpy.meshgrid(numpy.arange(x), numpy.arange(y))
ax.plot_surface(x, y, R0, cmap='hot')
ax.set_xlabel('Correctors')
ax.set_ylabel('Bpms')

In [ ]:
R0[1:5,1:5]

We use the method ```LINAC_BBA.orbit_correction(R0, B0, threshold)```
* The response matrix
* The incoming beam
* threshold is a cut applied to the singular values of the reponse matrix relative to the largest singular value

In [ ]:
plt.figure()
nSeeds = 10
LINAC_BBA.align_elements() # zeros the offsets of all the elements
for i in range(nSeeds):
    print('Seed {}/{}\n'.format(i+1, nSeeds))  
    LINAC_BBA.scatter_elements('quadrupole', sigma_X, sigma_X, 0, sigma_ROLL, 0, 0, 'center')
    LINAC_BBA.reset_correctors()
    LINAC_BBA.orbit_correction(R0, B0, 0.01); 
    LINAC_BBA.track(B0)
    T = LINAC_BBA.get_transport_table('%S %emitt_x %emitt_y')  
    plt.plot(T[:,0], T[:,1], 'C00', linewidth=2)
    plt.plot(T[:,0], T[:,2], 'C01', linewidth=2)
plt.legend([r'$\epsilon_x$', r'$\epsilon_y$'])
plt.xlabel('s [m]')
plt.ylabel(r'$\epsilon_n$ [mm.mrad]')
plt.show()

The correction is extremely effective!

We can get the corrector strengths using the method ```LINAC_BBA.get_corrector_strengths()```, which returns T*mm

In [ ]:
LINAC_BBA.get_correctors_strengths()

## Dispersion-Free Steering
We change the RF phase to send a test beam with an energy different from the nominal. Dispersion-free steering aims to have nominal and test beams pass through the same BPM positions.

\begin{equation*}
\left(
\begin{array}{rl}
 & \mathbf{b}\\
\omega_d & \left(\mathbf{b}_1-\mathbf{b}\right)\\
% & \mathbf{0}
\end{array}
\right)=
\left(
\begin{array}{rl} & \mathbf{R_0}\\
\omega_d & \left(\mathbf{R_1} - \mathbf{R_0}\right)\\
%\omega_w & \mathbf{W}\\
%\beta & \mathbf{I}
\end{array}\right)\boldsymbol{\theta}.
\end{equation*}

Given a measured orbit and dispersive trajectory, the system of equations provides the correcting correctors' settings:
\begin{equation*}
\Delta\boldsymbol{\theta}=-\left(\begin{array}{rl}
 & \mathbf{R_{0}}\\
\omega_{d} & \left(\mathbf{R_{1}}-\mathbf{R_{0}}\right),
\end{array}\right)^{-1}\left(\begin{array}{rl}
 & \mathbf{b}\\
\omega_{d} & \left(\mathbf{b}_{1}-\mathbf{b}\right)
\end{array}\right),
\end{equation*}
where $\left(\,\cdots\,\right)^{-1}$ denotes the pseudo-inverse of the matrix.

In [ ]:
def change_linac_phase(LINAC, phid):
    #for rf in LINAC.get_rf_elements():
    #    rf.set_phid(phid) 
    rf = LINAC.get_rf_elements()
    rf[0].set_phid(phid)

def get_h_dispersion(Lattice, B0, phid):
    Lattice.track(B0)
    x0 = Lattice.get_transport_table('%mean_x')   
    change_linac_phase(Lattice, 0)
    Lattice.track(B0)
    change_linac_phase(Lattice, phid)
    x1 = Lattice.get_transport_table('%mean_x')
    return numpy.squeeze(x1) - numpy.squeeze(x0)

In [ ]:
change_linac_phase(LINAC_BBA, 0)
R1 = LINAC_BBA.get_response_matrix (B0)
change_linac_phase(LINAC_BBA, setup.phid)

Let's store the 4d emittance for the uncorrected machine, the orbit-corrected, and the dispersion-corrected (usually, one would look at emittance in X and Y separately; however, here for simplicity, we look at the emittance 4d).

In [ ]:
sigma_X = 0.100 # mm
sigma_Xbpms = 0.020 # mm

nSeeds = 10
LINAC_BBA.align_elements() # zeros the offsets of all the elements

wgt = 10 # weighting factor between orbit and dispersion correction
R = numpy.concatenate((R0, wgt * (R1 - R0)))

S = numpy.squeeze(LINAC_BBA.get_transport_table('%S'))

T_Emt_U = numpy.zeros((nSeeds, len(S))) # uncorrected
T_Emt_O = numpy.zeros((nSeeds, len(S)))
T_Emt_D = numpy.zeros((nSeeds, len(S)))

T_D_U = numpy.zeros((nSeeds, len(S))) # uncorrected
T_D_O = numpy.zeros((nSeeds, len(S)))
T_D_D = numpy.zeros((nSeeds, len(S)))

for i in range(nSeeds):

    print('Seed {}/{}\n'.format(i+1, nSeeds)) 

    LINAC_BBA.scatter_elements('quadrupole', sigma_X, sigma_X, 0, 0, 0, 0, 'center')
    LINAC_BBA.scatter_elements('rf_element', sigma_X, sigma_X, 0, 0, 0, 0, 'center')
    LINAC_BBA.scatter_elements('bpm', sigma_Xbpms, sigma_Xbpms, 0, 0, 0, 0, 'center')
    LINAC_BBA.reset_correctors()

    print('Uncorrected machine...')
    LINAC_BBA.track(B0)   
    T_Emt_U[i] = numpy.squeeze(LINAC_BBA.get_transport_table('%emitt_4d'))
    T_D_U[i] = get_h_dispersion(LINAC_BBA, B0, setup.phid)
    
    # Orbit correction
    print('Orbit correction...')
    LINAC_BBA.orbit_correction(R0, B0, 0.01)   
    T_Emt_O[i] = numpy.squeeze(LINAC_BBA.get_transport_table('%emitt_4d'))
    T_D_O[i] = get_h_dispersion(LINAC_BBA, B0, setup.phid)
    
    # Dispersion correction
    print('Dispersion correction...')  
    Bpm0 = LINAC_BBA.get_bpm_readings()
    
    # Track the test beam
    change_linac_phase(LINAC_BBA, 0)
    LINAC_BBA.track(B0)
    change_linac_phase(LINAC_BBA, setup.phid)
    # Get the dispersive orbit
    Bpm1 = LINAC_BBA.get_bpm_readings()

    # Prepare for the correction computation
    Bpm0 = Bpm0.flatten('F') # transform into 1-column vector
    Bpm1 = Bpm1.flatten('F')

    # Compute correction
    B = numpy.concatenate((Bpm0, wgt * (Bpm1 - Bpm0)))
    C = -scipy.linalg.pinv(R, rtol=0.01) @ B

    # C is a vector containing 2*Ncorrectors items
    C = numpy.reshape(C, (2, int(len(C)/2))).T # We need to convert it in a 2-column matrix with Ncorrectors rows.
    # Apply the correction
    LINAC_BBA.vary_correctors_strengths(C)

    # Track the beam to get the emittance
    LINAC_BBA.track(B0)
    T_Emt_D[i] = numpy.squeeze(LINAC_BBA.get_transport_table('%emitt_4d'))
    T_D_D[i] = get_h_dispersion(LINAC_BBA, B0, setup.phid)

In [ ]:
plt.figure()
S = numpy.squeeze(LINAC_BBA.get_transport_table('%S'))
plt.plot(S, numpy.mean(T_Emt_U, axis=0), label='Uncorrected')
plt.plot(S, numpy.mean(T_Emt_O, axis=0), label='Orbit corrected')
plt.plot(S, numpy.mean(T_Emt_D, axis=0), label='Dispersion corrected')
plt.xlabel('S [m]')
plt.ylabel('average emitt [mm.mrad]')
plt.legend()

In [ ]:
plt.figure()
plt.plot(S, numpy.mean(T_D_U, axis=0), label='Uncorrected')
plt.plot(S, numpy.mean(T_D_O, axis=0), label='Orbit corrected')
plt.plot(S, numpy.mean(T_D_D, axis=0), label= 'Dispersion corrected')
plt.xlabel('S [m]')
plt.ylabel('average Dx [m]')
plt.legend()